# Bowerbird Agents Model

## Rachel and Julia 
Key
Notes- Parameters contain underscores, while functions don't

SB: Stay at bower

FG: Foraging

MT: Maraud travel (travel to rival's bower)

MA: Maraud action (destroy bower if absent, have antagonistic interaction in present)

MR: Maraud return (return to own bower)

RB: Repair own bower

a=-1: denotes a staying at bower action on ticket

a=-2: denotes a foraging action on ticket

a=-3: denotes a female visiting action on a ticket

a=-4: denotes travel to another male's bower

a=-5: denotes marauding of another male's bower

a=-6: denotes returning from another male's bower

a=-7: denotes a bower repair action on a ticket

target: the male an action is preformed on. For maurading, the target is the bird under potential attack. For mating, target is male being mated with. For other activities other then maurading and mating, owner and target are the same.

owner: The male or female actively performing an action. For mating, the female is the owner. For all other activities, the owner is male.

networkwriter: generates network where everybird is connected

addtotimeline: adds tickets to timeline

travel_times_linear_p: generates a matrix that contains the probabilities of travelling to a given a bower 
if the relationship between distance and travel preference is linear

improb: The probability of traveling improb_distance or less

improb_distance: The distance at which there is only a (1-improb)% chance of choosing to travel

lamb: lambda calculated by solving improb=1-numpy.exp(-lamb*improb_distance)

bower_states: options are 1 (bower intact) and 0 (bower destroyed-will never be the case when all guarders) and another value for time that mating will end (assuming mating is happening)

male_states: options are [leave_time] (male present at bower) and 0 (male absent from bower) NOTE: Want to update male_states to include targ for the purposes of modifying tickets due to female visits (when we introduce them).

fitness_states: keeps track of number of matings a given male has had

strategy_states: Given the option of SB and MT, will choose MT strategy_states proportion of the time

males: total number of male bowerbirds in the network

male_dist: the males by males matrix with distances between each male

tau: Length of time an activity takes. If a foraging ticket has a tau of 0.5 and occurs at t=1, then the bird is foraging for 30 minutes, at which point a SB activity will start (at t=1.5).

t_court: the amount of time it takes a female to court+mate with a male, generated from a normal distribution
not_maraud_time: the time added to SB by guarders

t_max: the maximum time 

F_per_M: the number of sexualy mature females per sexually mature male

long_FV_wait_time: The time it takes for a female to return if the recents list is filled but she doesn't mate

timeline: A sorted dictionary containing tickets with times, taus, actions, owners, and target. It's sorted by time, and secondarily by owner (if the times on the tickets are identical)





Note to self: think of female visit tickets as female travel tickets
The time on the ticket represents the time at which the female arrives at the male's bower (finishes traveling to it)

In [1]:
import math
from sortedcontainers import SortedDict
import random
import numpy 
import matplotlib.pyplot as plt
from scipy.stats import truncnorm

In [2]:
# Global Parameters:
males = 100
t_max = 12 #2 months in hrs (assume no nights so 12 hr = 1 day)
timeline = SortedDict() #New and improved timeline (using a sorted dictionary)!

FV_param = [0, t_max/2] #5days, tmax/3 #0.2 #males/0.19 #totally random
long_FV_wait_time=12

FG_k=1.5 #the shape of the gamma distribution rv used to generate FG taus
FG_theta=5 #the scale of the gamma distribution rv used to generate FG taus
FG_divisor=60

SB_param = 1.5 #larger values lead to bowerstay ending earlier, because taus are smaller

RB_param = 6 #made up -- takes 30mins (every time -- no distribution) to repair bower

MA_param = 0.1 #made up -- takes 6mins (every time -- no distribution) to maraud bower

#taus for in-between next_forages
FG_tau_mean, FG_tau_std = .4, .167 #mean and sd of truncated normal distribution rv to find a male's time until next FG
FG_tau_range = [0, 1] #maximum and minimum FG taus
FG_tau_norm_range = [(FG_tau_range[0] - FG_tau_mean) / FG_tau_std, (FG_tau_range[1] - FG_tau_mean) / FG_tau_std] #normalized

#taus for RB and SB
RBSB_tau_mean, RBSB_tau_std = .1583, .09755 #mean and sd of truncated normal distribution rv to find a male's time until next FG
RBSB_tau_range = [0,.5] #maximum and minimum FG taus
RBSB_tau_norm_range = [(RBSB_tau_range[0] - RBSB_tau_mean) / RBSB_tau_std, (RBSB_tau_range[1] - RBSB_tau_mean) / RBSB_tau_std] #normalized

next_forage = FG_tau_std * truncnorm.rvs(FG_tau_norm_range[0], FG_tau_norm_range[1], size=males) + FG_tau_mean
bower_states = [0] * males
male_states = [0] * males 
strategy_states=[0]*males
mating_states = [0] * males
fitness_states = numpy.array([0] * males)
success_rate = 1
success_times = [] #going to change this to be a vector of times when the female leaves (at this point, sucessful mating has occured)
recents_list = []
max_visits = 6 #STEEEEVEEEE
bird_speed = 12 * 3600 #m/hr (12m/s)
x_dim, y_dim = 400, 500 #dimensions of environment
F_per_M = 3 #number of sexually mature females per sexually mature males in a bowerbird population
num_sims = 1
not_maraud_time = 0.15

d={} 

for i in range(males):
    d["next_forages{0}".format(i)]=[]
    d["forage_times{0}".format(i)]=[]

In [3]:
def ticketgenerator(t, tau, ow, ac, targ):
    ticket = {
        'time': t, #time at which the activity starts
        'tau': tau, #how long the activity lasts
        'owner': ow, #who is doing the activity (could be a female if action=-3)
        'action': ac, #which activity (see key)
        'target': targ, #target of the activity (owner=target unless action=-3,-4,-5, or -6)
    }
    return ticket

In [4]:
#Adds tickets to timeline- sorts by time
def addtotimeline(ticket):
    global timeline
    timeline[(ticket["time"], ticket["owner"])] = ticket

In [5]:
# creation of the environment

def envgenerator(males, x_dim, y_dim):
    Xs = numpy.random.rand(males) * x_dim
    Ys = numpy.random.rand(males) * y_dim
    return [Xs,Ys]

def dists(xy, bird_speed):
    male_dist = numpy.zeros(males * males).reshape((males, males))
    travel_times = numpy.zeros(males * males).reshape((males, males))
    for i in range(males):
        for j in range(i + 1, males):
            dist = math.sqrt((xy[0][j] - xy[0][i]) ** 2 + (xy[1][j] - xy[1][i]) ** 2)
            travel = dist / bird_speed
            male_dist[j][i] = dist
            male_dist[i][j] = dist
            travel_times[j][i] = travel
            travel_times[i][j] = travel
    return [male_dist,travel_times]

# the probability of choosing a neighbor at distance x is proportional to exp(-\lambda x)
# choose lambda such that 99% of the mass is before 800 meters
improb = 0.99
improb_distance = 800
lamb = -math.log(1 - improb) / improb_distance

#will write female preference based on cumulative exponential decay (lambda=.00576)
def preferences(male_dist, males, lamb):
    # compute exponential of each coefficient
    visit_preferences = numpy.exp(-lamb * male_dist)
    # remove the identity matrix (exp(0) = 1)
    visit_preferences = visit_preferences - numpy.eye(males)
    # make rows sum to one
    visit_preferences = (visit_preferences.transpose() / numpy.sum(visit_preferences, 1)).transpose()
    return visit_preferences

In [6]:
# function for determining the next time based on our rate parameters
def nexttau(action, ow, targ): 
    switcher = { 
        -1: RBSB_tau_std*truncnorm.rvs(RBSB_tau_norm_range[0], RBSB_tau_norm_range[1])+RBSB_tau_mean, #choose when to leave bower (generate a tau for bower stay)
        -2: numpy.random.gamma(FG_k, FG_theta)/FG_divisor, #choose when to stop foraging (generate a tau for foraging)
        -4: travel_times[ow][targ],
        -5: MA_param, #in the future we'll do something with it
        -6: travel_times[targ][ow],
        -7: RBSB_tau_std*truncnorm.rvs(RBSB_tau_norm_range[0], RBSB_tau_norm_range[1])+RBSB_tau_mean,
    }
    new_tau=switcher.get(action)
    return new_tau

def nextticket(old_tic, new_ac, new_targ): #returns new ticket after ensuring it doesn't exceed t_max
    old_t=old_tic['time']
    new_tic={}
    if math.isclose(old_t, t_max, rel_tol=0, abs_tol=.0000001)==0: #if old_t is not essentially t_max
        ow=old_tic['owner']
        new_tau=nexttau(new_ac, ow, new_targ)
        end_t=old_t+new_tau #this time is the time when the action has ended
        if end_t>t_max: 
            new_tau=new_tau-(end_t-t_max) #modify the new_tau so end_t will be t_max
            end_t=old_t+new_tau #recalculate end_t
        new_tic=ticketgenerator(end_t, new_tau, ow, new_ac, new_targ) #now the time represents the end time for the action
    return new_tic


In [7]:

def malestatehandler(new_tic): #calls functions to change states of males i.e. for bower destruction, absence from bower
    ac=new_tic['action']
    if ac==-2 or ac==-4: #forage or maraud travel 
        male_states[new_tic['owner']]=0 #male_states of the ticket's owner is updated to show absence from bower
    elif ac==-1: #stay at bower
        male_states[new_tic['owner']]=new_tic['time'] #male_states of the ticket's owner becomes the time at which the male will leave the bower
    elif ac==-5: #maraud action
        targ=new_tic['target']
        if bower_states[targ]==0 and male_states[targ]==0:
            bower_states[targ]=-1*RB_param
    elif ac==-7: #repair bower
        ow=new_tic['owner']
        tau=new_tic['tau']
        if bower_states[ow]+tau>0:
            new_tic['time']-=bower_states[ow]+tau #think about it more in the AM :)
            tau=-1*bower_states[ow]
            new_tic['tau']=tau
        bower_states[ow]+=tau
        male_states[ow]=new_tic['time'] #although it doesn't matter from an FV POV
    else:
        pass

   

In [8]:

    
def femalestatehandler(tic): #Handles the male states in response to female visits
    targ=tic['target']
    t=tic['time']
    SB_time=male_states[targ]
    next_tic={}
    if bower_states[targ]==0 and SB_time!=0 and mating_states[targ]<t: #if the bower is intact, the male is there, and is not mating 
        fitness_states[targ]+=1 #add to the males' fitness_states (a count of succesful matings)
        mating_end=.25+t #can use dist instead of .25
        if t>SB_time: #if the time on the tic is greater than the stay at bower time
            old_tau=timeline[(SB_time, targ)]['tau'] #access the tau of the SB_tic -- we will use it to make a new one
            timeline[(SB_time, targ)]['action']=1 #nullify currently scheduled SB_tic
            #now make a new SB_tic with modified tau and time (so that male leaves right after finishing mating)
            truncator=0
            if mating_end>t_max:
                truncator=mating_end-t_max  #Used to ensure the times won't exceed t_max
            SB_tau=old_tau+(mating_end-SB_time)-truncator #update tau to reflect the proper tau 
            SB_time=mating_end-truncator #update the time to reflect the proper end time
            SB_tic=ticketgenerator(SB_time, SB_tau, targ, -1, targ) #generate a corrected SB_tic with the proper end time
            addtotimeline(SB_tic) #Add the ticket to the timeline
        mating_states[targ]=mating_end #update the mating state of the male to the mating end time (so other females can't mate with male)
        male_states[targ]=SB_time #update the male state to the updated SB_time
    else: #if female does not successfully mate
        recents_list=d["rl{0}".format(ow)]
        recents_list.append(targ)
        if len(recents_list)==min(max_visits, males): #if she's already visited her max # of males and not mated, reset recents and use nexttau
            recents_list=[]
            new_FV_targ=numpy.random.choice(list(range(males)), p=visit_preferences[targ])
            new_FV_tau=long_FV_wait_time
            new_FV_time=t+new_FV_tau #she goes to another male after waiting some time (nexttau), courting takes no time   
        else: #otherwise find a male not in recents and use travel_times
            new_FV_targ=-1 #just so that the code goes into the while loop the first iteration
            while(new_FV_targ in recents_list or new_FV_targ==-1):
                new_FV_targ=numpy.random.choice(list(range(males)), p=visit_preferences[targ]) #choose a male based on preference (a function of distance)
            new_FV_tau=travel_times[targ][new_FV_targ]
            new_FV_time=t+new_FV_tau #she goes directly to this male
        if new_FV_time<t_max:
            
            next_tic=ticketgenerator(new_FV_time, new_FV_tau, ow, -3, new_FV_targ)
    return next_tic


In [9]:
#choose what action / sequence of actions to do next
def decider(tic):
    ow = tic['owner']
    ac = tic['action'] 
    t = tic['time']
    targ=ow #will be reset in the case of -4
    if t>next_forage[ow]:
        d["forage_times{0}".format(ow)].append(t)
        #print("t is greater than next_FG[{:f}]: t={:f}, next_FG={:f}".format(ow, t, next_forage[ow]))
        new_ac=-2 #forage
        d["next_forages{0}".format(ow)].append(next_forage[ow])
        next_forage[ow] = t+FG_tau_std*truncnorm.rvs(FG_tau_norm_range[0], FG_tau_norm_range[1])+FG_tau_mean #forage 30 times / day on average (but underestimates)
    elif bower_states[ow]<0:
        new_ac=-7 #repair bower
    else:
        if random.random()<strategy_states[ow]: #if male chooses to maraud 
            targ=numpy.random.choice(list(range(males)), p=visit_preferences[ow])
            new_ac=-4 #maurad travel
        else: #if male chooses to stay at bower
            new_ac=-1 #stay at bower
    new_tic=nextticket(tic, new_ac, targ) #ONE IDEA -- separate ticket generation and adding to timeline
    return new_tic

In [10]:
xy = envgenerator(males, x_dim, y_dim)

travel_mats=dists(xy, bird_speed)
male_dist=travel_mats[0]
travel_times=travel_mats[1]

visit_preferences=preferences(male_dist, males, lamb)

In [11]:
for i in range(males):
    addtotimeline(ticketgenerator(0.0, 0.0, i, -2, i))

# for i in range(males*F_per_M):
#     first_time=numpy.random.uniform(FV_param[0], FV_param[1])
#     addtotimeline(ticketgenerator(first_time, 0.0, i, -3, numpy.random.choice(list(range(males)))))
#     d["rl{0}".format(i)]=[]
# print(timeline)

In [12]:

acc=0
new_tic=ticketgenerator(0.0, 0.0, 0, -2, 0) #for testing
for key in timeline:
    acc+=1
    print(acc)
    tic=timeline[key]
    print(new_tic)
    print(tic)
    ac=tic['action']
    ow=tic['owner']
    targ=tic['target']
    if ac!=-3:
        if ac==-4 or ac==-5:
            #generate a -5 or -6 tic as new_tic and pass it in
            male_tic=nextticket(tic, ac-1, targ)
        else:
            male_tic=decider(tic)
        if male_tic=={}:
            print("done (for some owner)!")
        else:
            malestatehandler(male_tic)
            addtotimeline(male_tic)
            new_tic=male_tic
    else:
        #d["rl{0}".format(ow)]=FVtickethandler(next_tic, d["rl{0}".format(ow)]) 
        female_tic=femalestatehandler(tic)
        if female_tic=={}:
            print("done (for some owner)!")
        else:
            addtotimeline(female_tic)
            new_tic=female_tic


1
{'time': 0.0, 'tau': 0.0, 'owner': 0, 'action': -2, 'target': 0}
{'time': 0.0, 'tau': 0.0, 'owner': 0, 'action': -2, 'target': 0}
2
{'time': 0.2820292878647374, 'tau': 0.2820292878647374, 'owner': 0, 'action': -1, 'target': 0}
{'time': 0.0, 'tau': 0.0, 'owner': 1, 'action': -2, 'target': 1}
3
{'time': 0.19648396598745044, 'tau': 0.19648396598745044, 'owner': 1, 'action': -1, 'target': 1}
{'time': 0.0, 'tau': 0.0, 'owner': 2, 'action': -2, 'target': 2}
4
{'time': 0.3430177759936252, 'tau': 0.3430177759936252, 'owner': 2, 'action': -1, 'target': 2}
{'time': 0.0, 'tau': 0.0, 'owner': 3, 'action': -2, 'target': 3}
5
{'time': 0.18526022483138946, 'tau': 0.18526022483138946, 'owner': 3, 'action': -1, 'target': 3}
{'time': 0.0, 'tau': 0.0, 'owner': 4, 'action': -2, 'target': 4}
6
{'time': 0.21889638752935456, 'tau': 0.21889638752935456, 'owner': 4, 'action': -1, 'target': 4}
{'time': 0.0, 'tau': 0.0, 'owner': 5, 'action': -2, 'target': 5}
7
{'time': 0.09704316648948295, 'tau': 0.09704316648

{'time': 0.4532511696936698, 'tau': 0.01748746537807944, 'owner': 54, 'action': -2, 'target': 54}
{'time': 0.4363993172401654, 'tau': 0.21996749081422612, 'owner': 39, 'action': -1, 'target': 39}
311
{'time': 0.5226199942653249, 'tau': 0.08622067702515951, 'owner': 39, 'action': -1, 'target': 39}
{'time': 0.43822098219189215, 'tau': 0.22407922736869762, 'owner': 48, 'action': -1, 'target': 48}
312
{'time': 0.4586078000037115, 'tau': 0.020386817811819332, 'owner': 48, 'action': -2, 'target': 48}
{'time': 0.4392948287275741, 'tau': 0.12126888377579517, 'owner': 56, 'action': -1, 'target': 56}
313
{'time': 0.5967546391736489, 'tau': 0.1574598104460748, 'owner': 56, 'action': -1, 'target': 56}
{'time': 0.44063331859033905, 'tau': 0.262135380767202, 'owner': 78, 'action': -1, 'target': 78}
314
{'time': 0.8419696460858463, 'tau': 0.40133632749550735, 'owner': 78, 'action': -2, 'target': 78}
{'time': 0.44071555666533635, 'tau': 0.23580247757913292, 'owner': 8, 'action': -1, 'target': 8}
315
{

515
{'time': 0.91526500148878, 'tau': 0.17037894585547395, 'owner': 21, 'action': -1, 'target': 21}
{'time': 0.745162752550624, 'tau': 0.03204155339033768, 'owner': 92, 'action': -2, 'target': 92}
516
{'time': 1.0156416320033366, 'tau': 0.27047887945271254, 'owner': 92, 'action': -1, 'target': 92}
{'time': 0.7456692942468864, 'tau': 0.09701423605448403, 'owner': 81, 'action': -1, 'target': 81}
517
{'time': 0.9054414207655743, 'tau': 0.15977212651868786, 'owner': 81, 'action': -1, 'target': 81}
{'time': 0.7470880190278542, 'tau': 0.18538441937238723, 'owner': 28, 'action': -2, 'target': 28}
518
{'time': 1.0092864523808385, 'tau': 0.2621984333529842, 'owner': 28, 'action': -1, 'target': 28}
{'time': 0.7477771199951404, 'tau': 0.29412358150576823, 'owner': 40, 'action': -1, 'target': 40}
519
{'time': 0.8143315813839919, 'tau': 0.06655446138885147, 'owner': 40, 'action': -2, 'target': 40}
{'time': 0.7498269033626818, 'tau': 0.2620926920947199, 'owner': 49, 'action': -1, 'target': 49}
520
{

686
{'time': 1.192198484429102, 'tau': 0.19548174355858888, 'owner': 61, 'action': -2, 'target': 61}
{'time': 0.9974281302637129, 'tau': 0.21967313856874277, 'owner': 33, 'action': -2, 'target': 33}
687
{'time': 1.091198342128386, 'tau': 0.09377021186467303, 'owner': 33, 'action': -1, 'target': 33}
{'time': 0.9983715487854902, 'tau': 0.03900931991160285, 'owner': 47, 'action': -2, 'target': 47}
688
{'time': 1.2717876070006109, 'tau': 0.2734160582151207, 'owner': 47, 'action': -1, 'target': 47}
{'time': 0.9985224276391461, 'tau': 0.15039239164686088, 'owner': 43, 'action': -1, 'target': 43}
689
{'time': 1.170389025849339, 'tau': 0.17186659821019298, 'owner': 43, 'action': -2, 'target': 43}
{'time': 1.00013082199966, 'tau': 0.16297420030590454, 'owner': 56, 'action': -1, 'target': 56}
690
{'time': 1.2692171005396335, 'tau': 0.2690862785399734, 'owner': 56, 'action': -1, 'target': 56}
{'time': 1.001909346597266, 'tau': 0.09121901927417976, 'owner': 10, 'action': -1, 'target': 10}
691
{'ti

850
{'time': 1.2892302991149958, 'tau': 0.028129834515440377, 'owner': 23, 'action': -2, 'target': 23}
{'time': 1.2626433662532008, 'tau': 0.1488054536651341, 'owner': 75, 'action': -2, 'target': 75}
851
{'time': 1.398645832867378, 'tau': 0.13600246661417723, 'owner': 75, 'action': -2, 'target': 75}
{'time': 1.2647381427350746, 'tau': 0.20525749492715947, 'owner': 85, 'action': -1, 'target': 85}
852
{'time': 1.5564789418017382, 'tau': 0.2917407990666636, 'owner': 85, 'action': -2, 'target': 85}
{'time': 1.2652424846298371, 'tau': 0.1483143804907952, 'owner': 37, 'action': -1, 'target': 37}
853
{'time': 1.3665811953775295, 'tau': 0.10133871074769246, 'owner': 37, 'action': -2, 'target': 37}
{'time': 1.2672898646223123, 'tau': 0.18198203824712678, 'owner': 13, 'action': -1, 'target': 13}
854
{'time': 1.2897022295928726, 'tau': 0.02241236497056036, 'owner': 13, 'action': -2, 'target': 13}
{'time': 1.2679860568965697, 'tau': 0.1162557992592021, 'owner': 86, 'action': -1, 'target': 86}
855


...

{'time': 4.422646904225402, 'tau': 0.22363092755644542, 'owner': 32, 'action': -1, 'target': 32}
{'time': 4.19902548783284, 'tau': 0.2500475476470568, 'owner': 17, 'action': -1, 'target': 17}
13967
{'time': 4.274749454196915, 'tau': 0.0757239663640749, 'owner': 17, 'action': -1, 'target': 17}
{'time': 4.199182354998027, 'tau': 0.2304592698947246, 'owner': 46, 'action': -1, 'target': 46}
13968
{'time': 4.495791486100958, 'tau': 0.2966091311029311, 'owner': 46, 'action': -1, 'target': 46}
{'time': 4.19955854028615, 'tau': 0.1916165474324996, 'owner': 83, 'action': -1, 'target': 83}
13969
{'time': 4.436010467624748, 'tau': 0.23645192733859832, 'owner': 83, 'action': -1, 'target': 83}
{'time': 4.1999424471898665, 'tau': 0.3320569424160252, 'owner': 44, 'action': -1, 'target': 44}
13970
{'time': 4.358428418518733, 'tau': 0.15848597132886705, 'owner': 44, 'action': -1, 'target': 44}
{'time': 4.19999052202564, 'tau': 0.11435102797034671, 'owner': 78, 'action': -1, 'target': 78}
13971
{'time':

{'time': 4.411344630809762, 'tau': 0.1586559148409793, 'owner': 90, 'action': -1, 'target': 90}
{'time': 4.252955349459405, 'tau': 0.2237603302624646, 'owner': 21, 'action': -1, 'target': 21}
14299
{'time': 4.27723563317249, 'tau': 0.024280283713084883, 'owner': 21, 'action': -1, 'target': 21}
{'time': 4.252997020289797, 'tau': 0.09345406832793185, 'owner': 81, 'action': -1, 'target': 81}
14300
{'time': 4.436148440057327, 'tau': 0.18315141976752977, 'owner': 81, 'action': -1, 'target': 81}
{'time': 4.252999425604009, 'tau': 0.15046992115408564, 'owner': 18, 'action': -1, 'target': 18}
14301
{'time': 4.47362596347755, 'tau': 0.2206265378735414, 'owner': 18, 'action': -1, 'target': 18}
{'time': 4.253010565206122, 'tau': 0.07293458600657018, 'owner': 7, 'action': -1, 'target': 7}
14302
{'time': 4.45200983860269, 'tau': 0.19899927339656823, 'owner': 7, 'action': -1, 'target': 7}
{'time': 4.253334230911843, 'tau': 0.02480451458329075, 'owner': 45, 'action': -1, 'target': 45}
14303
{'time': 

14466
{'time': 4.431810007679575, 'tau': 0.15342143963990276, 'owner': 36, 'action': -1, 'target': 36}
{'time': 4.278552383453829, 'tau': 0.07160493805864478, 'owner': 44, 'action': -1, 'target': 44}
14467
{'time': 4.591300471597499, 'tau': 0.31274808814367044, 'owner': 44, 'action': -1, 'target': 44}
{'time': 4.278674179900408, 'tau': 0.16325017626068464, 'owner': 8, 'action': -1, 'target': 8}
14468
{'time': 4.53447701008751, 'tau': 0.2558028301871027, 'owner': 8, 'action': -1, 'target': 8}
{'time': 4.278990430431164, 'tau': 0.09744046997242645, 'owner': 6, 'action': -1, 'target': 6}
14469
{'time': 4.437650045597188, 'tau': 0.15865961516602411, 'owner': 6, 'action': -1, 'target': 6}
{'time': 4.2790898028846875, 'tau': 0.16898728022895143, 'owner': 91, 'action': -1, 'target': 91}
14470
{'time': 4.411573559922277, 'tau': 0.1324837570375897, 'owner': 91, 'action': -1, 'target': 91}
{'time': 4.279127296678358, 'tau': 0.2159238683078742, 'owner': 60, 'action': -1, 'target': 60}
14471
{'tim

{'time': 4.310212288510096, 'tau': 0.14159281596108514, 'owner': 91, 'action': -1, 'target': 91}
14639
{'time': 4.610759350847273, 'tau': 0.30054706233717754, 'owner': 91, 'action': -1, 'target': 91}
{'time': 4.310213814112094, 'tau': 0.15053354601211108, 'owner': 14, 'action': -1, 'target': 14}
14640
{'time': 4.373392397955647, 'tau': 0.06317858384355308, 'owner': 14, 'action': -1, 'target': 14}
{'time': 4.310377077312166, 'tau': 0.18148808810595515, 'owner': 59, 'action': -1, 'target': 59}
14641
{'time': 4.432891921971558, 'tau': 0.12251484465939187, 'owner': 59, 'action': -1, 'target': 59}
{'time': 4.310402024436543, 'tau': 0.19752349570200298, 'owner': 52, 'action': -1, 'target': 52}
14642
{'time': 4.664524181740707, 'tau': 0.3541221573041641, 'owner': 52, 'action': -1, 'target': 52}
{'time': 4.310756210009572, 'tau': 0.16743169832774163, 'owner': 50, 'action': -2, 'target': 50}
14643
{'time': 4.365079056160474, 'tau': 0.05432284615090252, 'owner': 50, 'action': -1, 'target': 50}
{

KeyboardInterrupt: 

In [13]:
print(timeline)
print(len(timeline))

SortedDict({(0.0, 0): {'time': 0.0, 'tau': 0.0, 'owner': 0, 'action': -2, 'target': 0}, (0.0, 1): {'time': 0.0, 'tau': 0.0, 'owner': 1, 'action': -2, 'target': 1}, (0.0, 2): {'time': 0.0, 'tau': 0.0, 'owner': 2, 'action': -2, 'target': 2}, (0.0, 3): {'time': 0.0, 'tau': 0.0, 'owner': 3, 'action': -2, 'target': 3}, (0.0, 4): {'time': 0.0, 'tau': 0.0, 'owner': 4, 'action': -2, 'target': 4}, (0.0, 5): {'time': 0.0, 'tau': 0.0, 'owner': 5, 'action': -2, 'target': 5}, (0.0, 6): {'time': 0.0, 'tau': 0.0, 'owner': 6, 'action': -2, 'target': 6}, (0.0, 7): {'time': 0.0, 'tau': 0.0, 'owner': 7, 'action': -2, 'target': 7}, (0.0, 8): {'time': 0.0, 'tau': 0.0, 'owner': 8, 'action': -2, 'target': 8}, (0.0, 9): {'time': 0.0, 'tau': 0.0, 'owner': 9, 'action': -2, 'target': 9}, (0.0, 10): {'time': 0.0, 'tau': 0.0, 'owner': 10, 'action': -2, 'target': 10}, (0.0, 11): {'time': 0.0, 'tau': 0.0, 'owner': 11, 'action': -2, 'target': 11}, (0.0, 12): {'time': 0.0, 'tau': 0.0, 'owner': 12, 'action': -2, 'targe

In [ ]:
#timeline2=SortedDict()

#def addtotimeline2(ticket):
#    global timeline2
#    timeline2[(ticket["owner"], ticket["time"])] = ticket
    

#for key in timeline:
#    tic=timeline[key]
#    addtotimeline2(tic)
    

In [ ]:
#print(timeline2)

In [ ]:
#plt.figure()
#for i in range(males):
#    dic=d["next_forages{0}".format(i)]
#    print(dic)
#    line=[i]*len(dic)
#    plt.plot(dic,line,'.')


In [ ]:
# plt.figure()
# for i in range(males):
#     dic=d["forage_times{0}".format(i)]
#     print(len(dic))
#     print(dic)
#     line=[i]*len(dic)
#     plt.plot(dic,line,'.')


In [ ]:
# #testing femalestatehandler(without the implementation of female_tics)

# def femalestatehandler(new_tic): #here the t is the start time... idea for future: female start and end tics?
#     targ=new_tic['target']
#     t=new_tic['time']
#     SB_time=male_states[targ]
#     if bower_states[targ]==0 and SB_time!=0 and mating_states[targ]<t:
#         fitness_states[targ]+=1
#         mating_end=.25+t #can use dist instead of .25
#         if t>SB_time:
#             #print("t is less than mating end")
#             old_tau=timeline2[(SB_time, targ)]['tau'] #access the tau of the SB_tic -- we will use it to make a new one
#             timeline2[(SB_time, targ)]['action']=1 #nullify currently scheduled SB_tic
#             #now make a new SB_tic with modified tau and time (so that male leaves right after finishing mating)
#             truncator=0
#             if mating_end>t_max:
#                 truncator=mating_end-t_max  
#             SB_tau=old_tau+(mating_end-SB_time)-truncator
#             SB_time=mating_end-truncator
#             SB_tic=ticketgenerator(SB_time, SB_tau, targ, -1, targ)
#             addtotimeline2(SB_tic)
#         mating_states[targ]=mating_end
#         male_states[targ]=SB_time
        

# timeline2=SortedDict()

# def addtotimeline2(ticket):
#     global timeline2
#     timeline2[(ticket["time"], ticket["owner"])] = ticket
    
# bower_states = [0] * males
# male_states = [1] * males 
# mating_states = [0] * males

# for i in range(males):
#     addtotimeline2(ticketgenerator(1, 1, i, -1, i))
# print(timeline2)

# female_tic=ticketgenerator(0.7, 0.03, 5, -3, 0) #works at both .7 and .9 (when SB_tic must be re-written)
# print(FVstatehandler(female_tic))

# print(male_states)
# print(mating_states)
# print(timeline2)

In [ ]:
#print(female_tic)

In [ ]:
print(fitness_states)

In [ ]:
print(len(timeline)/t_max)

In [ ]:
len(timeline)

In [ ]:
nexttau(-1,1,2)

In [ ]:
nexttau(-2,1,2)

In [ ]:
nexttau(-4,1,2)

In [ ]:
nexttau(-5,1,2)

In [ ]:
nexttau(-7,1,2)